In [37]:
%load_ext autoreload
%autoreload 2
import jax
from jax import random
from environments import RodentSingleClipTrack, HumanoidTracking
import numpy as np
import mediapy as media
import jax.numpy as jp

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


#### Humanoid env

In [38]:
params = {
    "solver": "cg",
    "iterations": 6,
    "ls_iterations": 6,
    "clip_path": "humanoid_traj.p",
}

In [39]:
env = HumanoidTracking(params)

In [40]:
state = env.reset(jax.random.PRNGKey(0))

In [41]:
key = random.PRNGKey(0)
jit_step = jax.jit(env.step)
jit_reset = jax.jit(env.reset)

In [42]:
next = jit_reset(key)
print("starting rollout")
mu = 0
sigma = .1
rollout = []
for _ in range(500):
    _, key = jax.random.split(key)
    next = jit_step(next, mu + sigma * random.normal(key, shape=(env.sys.nu,)))
    rollout.append(next)

starting rollout


In [43]:
import mediapy as media
import os

os.environ["MUJOCO_GL"] = "glfw"
rollout_data = [s.pipeline_state for s in rollout]

video = env.render(rollout_data, camera='side', height=500, width=500)

media.show_video(video, fps=1.0 / env.dt)

This browser does not support the video tag.


#### Rodent env

In [2]:
params = {
    "scale_factor": .9,
    "solver": "cg",
    "iterations": 6,
    "ls_iterations": 3,
    "clip_path": "transform_snips_250_clip_750.p",
    "end_eff_names": [
        "foot_L",
        "foot_R",
        "hand_L",
        "hand_R",
    ],
}

# Creating env objects

In [3]:
env = RodentSingleClipTrack(params)

In [4]:
key = random.PRNGKey(0)
jit_step = jax.jit(env.step)
jit_reset = jax.jit(env.reset)
# next = env.step(state, random.uniform(key, shape=(env.sys.nu,)))

In [5]:
n = env.reset(key)

In [ ]:
obs = n.obs

In [109]:
obs.shape

(609,)

In [60]:
# res = jax.tree_util.tree_map(
#     lambda x: jax.lax.dynamic_slice_in_dim(x, 3, 4, axis=1),
#     env._ref_traj,
# )

In [61]:
jax.tree_util.tree_map(
    lambda x: print(x.shape),
    env._ref_traj,
)

(250, 3)
(250, 5, 3)
(250, 18, 3)
(250, 18, 4)
(250, 3)
(250, 4, 3)
(250, 67)
(250, 67)
(0,)
(250, 3)
(250, 4)
(0,)
(250, 3)


ReferenceClip(angular_velocity=None, appendages=None, body_positions=None, body_quaternions=None, center_of_mass=None, end_effectors=None, joints=None, joints_velocity=None, markers=None, position=None, quaternion=None, scaling=None, velocity=None)

In [62]:
env._ref_traj.body_positions[:,env.body_idxs]

Array([[[-0.05157034,  0.3405091 ,  0.07103304],
        [-0.04423911,  0.297583  ,  0.05947985],
        [-0.05854973,  0.29726464,  0.05947506],
        ...,
        [-0.06766652,  0.3676939 ,  0.05456821],
        [-0.05300185,  0.35287777,  0.0384187 ],
        [-0.06718285,  0.3718082 ,  0.01327727]],

       [[-0.05444217,  0.3449859 ,  0.07158838],
        [-0.05279249,  0.30190387,  0.0614456 ],
        [-0.06676881,  0.30457118,  0.05988254],
        ...,
        [-0.0607067 ,  0.37427917,  0.05398194],
        [-0.05153117,  0.3574425 ,  0.03587908],
        [-0.05690969,  0.38318592,  0.01352061]],

       [[-0.05978363,  0.35593086,  0.07326452],
        [-0.06929351,  0.3148967 ,  0.06476209],
        [-0.08140896,  0.32034692,  0.05943235],
        ...,
        [-0.052885  ,  0.3811076 ,  0.05077108],
        [-0.04858348,  0.36400667,  0.03116415],
        [-0.0398935 ,  0.39113626,  0.01167   ]],

       ...,

       [[ 0.04417997,  0.12506871,  0.06885403],
        [ 0

In [63]:
env._ref_traj.position.shape

(250, 3)

In [64]:
# def slice_arrays(start_index, end_index):
#     def slicer(x):
#         if isinstance(x, jp.ndarray):
#             return x[..., start_index:end_index]
#         return x
#     return slicer

# sliced_tree = jax.tree_map(slice_arrays(0, 5), env._ref_traj)
# sliced_tree.body_positions.shape

In [65]:
# start_index = 0
# end_index = 5
# sliced_clip = env._ref_traj.slice_clip(start_index, end_index)
# sliced_clip.center_of_mass.shape

In [66]:
5 + jp.arange(env._ref_traj_length)

Array([5, 6, 7, 8, 9], dtype=int32)

# Creating state objects & reset_fn, get_obs_fn
`reset_fn` and `get_obs_fn` is called when initilizing the environment and creating the state object

In [67]:
rng = random.PRNGKey(0)
state = env.reset(rng)

/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco

In [68]:
state.info['cur_frame']

Array(56, dtype=int32)

In [69]:
env._ref_traj.velocity[:, state.info['cur_frame']]

Array([ 0.0277672 ,  0.08380674,  0.02138875,  0.00653714, -0.02395846,
       -0.15192218,  0.00262782,  0.00265129, -0.03930293,  0.05484447,
        0.0218261 ,  0.01506135,  0.02508797,  0.06741397,  0.04323199,
       -0.02841055, -0.04715882,  0.06020367,  0.0104744 ,  0.00696592,
       -0.06255247, -0.03711618, -0.02833083, -0.00144839,  0.01545511,
        0.03185645, -0.04066043, -0.10863096, -0.06997176, -0.00802986,
        0.04102699, -0.00721775,  0.03914759,  0.05538873,  0.07378198,
        0.03505796,  0.01903474,  0.00744797, -0.0028722 , -0.01233071,
        0.04721247,  0.04758909,  0.02953112,  0.04170612,  0.02127364,
        0.03168434,  0.06975569,  0.03676414,  0.03934167, -0.02825595,
       -0.08189678, -0.06974339, -0.0704132 , -0.0150729 , -0.0171084 ,
       -0.06373338, -0.11344627, -0.0661049 ,  0.0049375 ,  0.03126971,
       -0.07830039,  0.01091771, -0.06837435, -0.04389212, -0.00356808,
        0.09577461,  0.01002178, -0.0432156 ,  0.03295243,  0.06

In [70]:
env.body_idxs

Array([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16,
       17], dtype=int32)

In [71]:
state.pipeline_state.xpos[:,0] # all x values
state.pipeline_state.xpos[env.body_idxs].shape

(18, 3)

In [72]:
env._ref_traj.body_positions.shape

(250, 18, 3)

In [73]:
env.body_idxs

Array([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16,
       17], dtype=int32)

In [74]:
state.pipeline_state.xpos[:, env.body_idxs].shape

(66, 18)

In [75]:
state.pipeline_state.xpos.shape

(66, 3)

In [76]:
state.pipeline_state.xpos[:,3000]

Array([ 0.        ,  0.07336916,  0.08591323,  0.08514435,  0.08337472,
        0.08050891,  0.07631666,  0.07148736,  0.0600691 ,  0.04907212,
        0.0357085 ,  0.01141115,  0.00976997,  0.05140926,  0.0303472 ,
        0.01621009,  0.01242737,  0.04458705,  0.03971803,  0.03498532,
        0.03018302,  0.02529153,  0.0201501 ,  0.01436727,  0.00860297,
        0.00285957, -0.0026444 , -0.00817518, -0.01355836, -0.01820275,
       -0.0214476 , -0.02409877, -0.02666723, -0.02905989, -0.03133695,
       -0.03361285, -0.03589554, -0.0382291 , -0.04062716, -0.04297147,
       -0.04523874, -0.04742804, -0.0494928 , -0.05139779, -0.05324481,
       -0.05499601, -0.05646563,  0.07530309,  0.074923  ,  0.07478291,
        0.07462545,  0.07372799,  0.07368456,  0.07301174,  0.07535487,
        0.06062561,  0.08270192,  0.06050065,  0.03644663,  0.01433735,
        0.00660772,  0.08368626,  0.06402209,  0.04349626,  0.02249428,
        0.01830076], dtype=float32)

In [77]:
state.pipeline_state.xpos[:, env.body_idxs][:,10]

Array([ 0.        ,  0.07336916,  0.08591323,  0.08514435,  0.08337472,
        0.08050891,  0.07631666,  0.07148736,  0.0600691 ,  0.04907212,
        0.0357085 ,  0.01141115,  0.00976997,  0.05140926,  0.0303472 ,
        0.01621009,  0.01242737,  0.04458705,  0.03971803,  0.03498532,
        0.03018302,  0.02529153,  0.0201501 ,  0.01436727,  0.00860297,
        0.00285957, -0.0026444 , -0.00817518, -0.01355836, -0.01820275,
       -0.0214476 , -0.02409877, -0.02666723, -0.02905989, -0.03133695,
       -0.03361285, -0.03589554, -0.0382291 , -0.04062716, -0.04297147,
       -0.04523874, -0.04742804, -0.0494928 , -0.05139779, -0.05324481,
       -0.05499601, -0.05646563,  0.07530309,  0.074923  ,  0.07478291,
        0.07462545,  0.07372799,  0.07368456,  0.07301174,  0.07535487,
        0.06062561,  0.08270192,  0.06050065,  0.03644663,  0.01433735,
        0.00660772,  0.08368626,  0.06402209,  0.04349626,  0.02249428,
        0.01830076], dtype=float32)

In [78]:
state.pipeline_state.qpos.shape

(74,)

In [79]:
state.obs.shape

(879,)

end effector position

In [80]:
state.pipeline_state.xpos[jp.array(env._end_eff_idx)]

Array([[-0.00912952,  0.4411053 ,  0.01141115],
       [-0.03021844,  0.414083  ,  0.01621009],
       [ 0.0780039 ,  0.40200663,  0.01433735],
       [ 0.08267315,  0.36600125,  0.02249428]], dtype=float32)

In [81]:
env._ref_traj.end_effectors.shape

(250, 4, 3)

# Creating step_fn, reward_fn, & termination_fn
`step_fn`, which calls `reward_fn` & `termination_fn` is only used when actually making action, not when setting up environment and state object

In [82]:
# rollout = [state.pipeline_state]
# ctrl = jax.numpy.array(np.random.uniform(-1,1, env.sys.nu))
# state = env.step(state, ctrl)
# rollout.append(state.pipeline_state)

In [83]:
# media.show_video(env.render(rollout,camera='close_profile'), fps=1.0 / env.dt)

In [84]:
next = jit_reset(key)
print("starting rollout")
mu = 0
sigma = .1
rollout = []
for _ in range(500):
    next = jit_step(next, mu + sigma * random.normal(key, shape=(env.sys.nu,)))
    rollout.append(next)

/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco

starting rollout


/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco

In [85]:
import mediapy as media
import os

os.environ["MUJOCO_GL"] = "glfw"
rollout_data = [s.pipeline_state for s in rollout]

video = env.render(rollout_data, camera='side_alt', height=500, width=500)

media.show_video(video, fps=1.0 / env.dt)

This browser does not support the video tag.


# Stepping Environment & Observe Changes in Frames

In [86]:
env = RodentSingleClipTrack(params)
reset_fn = jax.jit(jax.vmap(env.reset))
step_fn = jax.jit(jax.vmap(env.step))

n_envs = 16
key_envs = jax.random.split(key, n_envs)
env_state = reset_fn(key_envs)

/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/brax/io/mjcf.py:344: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  link = jax.tree_map(lambda x: x[1:].copy(), link)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/brax/io/mjcf.py:374: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  motion = jax.tree_map(lambda *x: np.concatenate(x), *motions)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/brax/io/mjcf.py:378: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  limit = jax.tree_map(lambda *x: np.concatenate(x), *limits)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitatio

In [87]:
env_state.info['cur_frame']

Array([41, 72, 54, 80, 56, 74, 38, 65, 69, 23, 20, 60, 55, 10, 89, 45],      dtype=int32)

In [88]:
mu = 0
sigma = 0.3
action =  mu + sigma * random.normal(key, shape=(n_envs, env.sys.nu))
new_state = step_fn(env_state, action)

/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco/mjx/_src/scan.py:65: DeprecationWarning: jax.tree_map is deprecated: use jax.tree.map (jax v0.4.25 or newer) or jax.tree_util.tree_map (any JAX version).
  return jax.tree_map(take, obj)
/Users/kevinb/Desktop/salk/rodent/VNL-Brax-Imitation-Main/.brax-imitation/lib/python3.10/site-packages/mujoco

In [89]:
new_state.info['cur_frame']

Array([42, 73, 55, 81, 57, 75, 39, 66, 70, 24, 21, 61, 56, 11, 90, 46],      dtype=int32)

# Testing Relative Functions
Instantiate `dm_contol` MultiClipMocapTracking Environment with ur ref_traj data, seems a bit challenging, using rodent trajectory is not applicable probably (observation tell).

In [91]:
# from dm_control import composer
# from dm_control.locomotion import arenas
# from walker import Rat
# from dm_control.locomotion.mocap import props
# from dm_control.locomotion.tasks.reference_pose import tracking
# from dm_control.locomotion.tasks.reference_pose import types
# import pickle
# import os
# from dm_control.utils import io as resources

# # with open('12_22_1_250_clip_0.p', 'rb') as f:
# #     ref_traj = pickle.load(f)

# file_name = '12_22_1_250_clip_0.h5'
# current_directory = os.getcwd()
# TEST_FILE_PATH = os.path.join(current_directory, file_name)

# task = tracking.MultiClipMocapTracking(
#         walker=Rat,
#         arena=arenas.Floor(),
#         ref_path=resources.GetResourceFilename(TEST_FILE_PATH),
#         ref_steps=(1, 2, 3, 4, 5),
#         min_steps=1,
#         dataset=types.ClipCollection(ids=('cmuv2019_001', 'cmuv2019_002')),
#         reward_type='comic',
#     )

# env = composer.Environment(task=task)

# env.reset()